# Práctica 5B: Missing Data Detective - California Housing
## Autor: Valentín Rodríguez
### UT2: Calidad & Ética | Práctica Alternativa

## 🎯 Objetivos Básicos
- Aprender a detectar y analizar datos faltantes (MCAR, MAR, MNAR)  
- Identificar outliers usando métodos estadísticos  
- Implementar estrategias de imputación apropiadas  
- Crear pipelines de limpieza reproducibles  
- Considerar aspectos éticos en el tratamiento de datos  

---

## 🔍 Nota Ética sobre Elección del Dataset

**¿Por qué California Housing y no Boston Housing?**

Se comenzó a utilizar el dataset de **Boston Housing**, pero a mitad del análisis se encontró documentación que incluía **problemas éticos** en dicho dataset:
- Variable "B" asume que auto-segregación racial impacta positivamente los precios
- Investigación original carecía de validez en sus asunciones
- Mantenedores de scikit-learn desaconsejan su uso excepto para educación ética
- Fue removido de scikit-learn desde versión 1.2+

**Decisión ética:** Se cambió a **California Housing** (1990) que proporciona un contexto similar (mercado inmobiliario estadounidense) sin las implicaciones éticas problemáticas, permitiendo un análisis riguroso y responsable.

---

## 📋 Lo que necesitas saber ANTES de empezar
- Conceptos básicos de **pandas** y **visualización**  
- Idea general de qué son los **datos faltantes**  
- Curiosidad por entender **patrones en la calidad de datos**  

---

## 🔍 Parte 1: Setup y Carga de Datos

### 📋 CONTEXTO DE NEGOCIO (CRISP-DM: Business Understanding)

### 🔗 Referencias oficiales:
- [Kaggle Data Cleaning - Handling Missing Values](https://www.kaggle.com)  
- [Pandas Documentation](https://pandas.pydata.org/docs/)  
- [Matplotlib Documentation](https://matplotlib.org/stable/contents.html)  
- [Seaborn Documentation](https://seaborn.pydata.org/)  
- [Scikit-learn Documentation](https://scikit-learn.org/stable/user_guide.html)  

---

## 🏠 Caso de negocio

- **Problema**: El dataset *California Housing* tiene datos faltantes y outliers que afectan las predicciones de precios.  
- **Objetivo**: Detectar patrones de *missing data* y outliers para limpiar el dataset.  
- **Variables**: `MEDV` (precio), `MedInc` (ingreso), `HouseAge` (edad), `AveRooms` (habitaciones), `Population` (población), etc.  
- **Valor para el negocio**: Datos más limpios = predicciones de precios inmobiliarios más confiables.


In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from scipy import stats
from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
import warnings
warnings.filterwarnings('ignore')

print("✅ Todas las librerías importadas correctamente")

# 3. Configurar visualizaciones
plt.style.use('seaborn-v0_8')  # estilo visual (ej: 'seaborn-v0_8', 'default', 'classic')
sns.set_palette("husl")  # paleta de colores (ej: 'husl', 'Set1', 'viridis')
plt.rcParams['figure.figsize'] = (12, 8)
plt.rcParams['font.size'] = 12

print("🎨 Configuración de visualizaciones lista!")


In [ ]:
# === CARGAR DATASET CALIFORNIA HOUSING ===

# 1. Cargar dataset desde sklearn
from sklearn.datasets import fetch_california_housing
california = fetch_california_housing()
df = pd.DataFrame(california.data, columns=california.feature_names)
df['MEDV'] = california.target  # Variable objetivo (precio mediano en unidades de $100K)

# Agregar columnas categóricas simuladas para el análisis
np.random.seed(42)

# Simular regiones de California
neighborhoods = ['Los Angeles', 'San Francisco', 'San Diego', 'San Jose', 'Oakland', 
                'Sacramento', 'Fresno', 'Long Beach', 'Bakersfield', 'Anaheim',
                'Santa Ana', 'Riverside', 'Stockton', 'Irvine']
df['NEIGHBORHOOD'] = np.random.choice(neighborhoods, size=len(df))

# Simular tipos de vivienda
house_types = ['Single Family', 'Townhouse', 'Condo', 'Multi-Family', 'Duplex']
df['HOUSE_TYPE'] = np.random.choice(house_types, size=len(df))

print("🏠 DATASET: California Housing")
print(f"   📊 Forma original: {df.shape}")
print(f"   📋 Columnas: {list(df.columns)}")

# 2. Crear missing data sintético para práctica
np.random.seed(42)  # para reproducibilidad

# Simular MCAR en AveOccup (8% missing aleatorio)
# "Los valores faltan al azar: que falte AveOccup no depende de la ocupación ni del propio valor"
missing_aveoccup = np.random.random(len(df)) < 0.08
df.loc[missing_aveoccup, 'AveOccup'] = np.nan

# Simular MAR en AveRooms (missing relacionado con HouseAge)
# "Los faltantes de AveRooms se concentran en edificios más antiguos (variable observada)"
old_buildings = df['HouseAge'] > df['HouseAge'].quantile(0.7)
df.loc[old_buildings, 'AveRooms'] = df.loc[old_buildings, 'AveRooms'].sample(frac=0.6, random_state=42)

# Simular MNAR en MEDV (missing relacionado con precio alto)
# "Los faltantes dependen del propio valor: quienes tienen precios altos no reportan precio"
high_price = df['MEDV'] > df['MEDV'].quantile(0.85)
df.loc[high_price, 'MEDV'] = df.loc[high_price, 'MEDV'].sample(frac=0.3, random_state=42)

print("\n🔍 Missing data sintético creado:")
print(df.isna().sum())  # método para contar valores faltantes por columna


In [ ]:
# === EXPLORACIÓN BÁSICA ===

# 1. Información general del dataset
print("=== INFORMACIÓN GENERAL ===")
print(df.info())  # método que muestra tipos de datos, memoria y valores no nulos

# 2. Estadísticas descriptivas
print("\n=== ESTADÍSTICAS DESCRIPTIVAS ===")
print(df.describe(include='all'))  # método que calcula estadísticas descriptivas

# 3. Tipos de datos
print("\n=== TIPOS DE DATOS ===")
print(df.dtypes)  # atributo que muestra tipos de datos por columna

# 4. Verificar missing data
print("\n=== MISSING DATA POR COLUMNA ===")
missing_count = df.isnull().sum()  # contar valores faltantes
missing_pct = (missing_count / len(df)) * 100  # calcular porcentaje

missing_stats = pd.DataFrame({
    'Column': df.columns,
    'Missing_Count': missing_count,
    'Missing_Percentage': missing_pct
})
print(missing_stats[missing_stats['Missing_Count'] > 0])

# 5. Análisis de memoria
print("\n=== ANÁLISIS DE MEMORIA ===")
total_bytes = df.memory_usage(deep=True).sum()  # método para memoria en bytes
print(f"Memoria total del DataFrame: {total_bytes / (1024**2):.2f} MB")

# 6. Análisis de duplicados
print("\n=== ANÁLISIS DE DUPLICADOS ===")
duplicates = df.duplicated()  # método para detectar filas duplicadas
print(f"Número de filas duplicadas: {duplicates.sum()}")
if duplicates.sum() > 0:
    print("Primeras 5 filas duplicadas:")
    print(df[df.duplicated()].head())  # método para filtrar duplicados


In [ ]:
# === ANÁLISIS DE PATRONES DE MISSING DATA ===

# 1. Filtrar solo columnas con missing data para visualización
missing_columns = df.columns[df.isnull().any()].tolist()  # método para detectar missing
print(f"Columnas con missing data: {len(missing_columns)}")
print(f"Columnas: {missing_columns}")

# 2. Visualización mejorada
plt.subplot(1, 1, 1)
if len(missing_columns) > 0:
    # Crear estadísticas de missing solo para columnas con missing data
    missing_count = df[missing_columns].isnull().sum()  # método para contar missing
    missing_pct = (missing_count / len(df)) * 100  # calcular porcentaje

    missing_stats_filtered = pd.DataFrame({
        'Column': missing_columns,
        'Missing_Count': missing_count,
        'Missing_Percentage': missing_pct
    }).sort_values('Missing_Percentage', ascending=False)

    # Crear gráfico de barras más limpio
    bars = plt.bar(range(len(missing_stats_filtered)), missing_stats_filtered['Missing_Percentage'], 
                   color='steelblue', alpha=0.7, edgecolor='black', linewidth=0.5)  # función para barras
    plt.title('Porcentaje de Missing por Columna - Boston Housing', fontsize=14, fontweight='bold')
    plt.xticks(range(len(missing_stats_filtered)), missing_stats_filtered['Column'], 
               rotation=45, ha='right')  # función para etiquetas del eje X

    plt.ylabel('Porcentaje de Missing (%)')
    plt.grid(True, alpha=0.3, axis='y')

    # Agregar valores en las barras
    for i, bar in enumerate(bars):
        height = bar.get_height()
        plt.text(bar.get_x() + bar.get_width()/2., height + 0.5,
                f'{height:.1f}%', ha='center', va='bottom', fontsize=10)
else:
    plt.text(0.5, 0.5, 'No hay missing data', ha='center', va='center', fontsize=16)
    plt.title('Porcentaje de Missing por Columna', fontsize=14, fontweight='bold')

# Distribución de missing por fila
plt.show()
plt.subplot(1, 1, 1)
missing_per_row = df.isnull().sum(axis=1)  # contar missing por fila
plt.hist(missing_per_row, bins=range(0, missing_per_row.max()+2), alpha=0.7, 
         edgecolor='black', color='lightcoral')  # función para histograma
plt.title('Distribución de Missing por Fila - Boston Housing', fontsize=14, fontweight='bold')
plt.xlabel('Número de valores faltantes por fila')
plt.ylabel('Frecuencia')
plt.grid(True, alpha=0.3, axis='y')

plt.tight_layout()
plt.savefig('boston-housing-missing-patterns.png', dpi=300, bbox_inches='tight')
plt.show()


In [ ]:
# === CLASIFICACIÓN MCAR/MAR/MNAR ===

print("=== ANÁLISIS DE TIPOS DE MISSING ===")

# 1. NOX: ¿MCAR o MAR?
print("\n1. NOX - Análisis de patrones:")
nox_missing = df['NOX'].isnull()  # método para detectar missing
print("Missing NOX por Neighborhood:")
print(df.groupby('NEIGHBORHOOD')['NOX'].apply(lambda x: x.isnull().sum()))  # contar missing por grupo

print("Missing NOX por House Type:")
print(df.groupby('HOUSE_TYPE')['NOX'].apply(lambda x: x.isnull().sum()))

# 2. RM: ¿MAR?
print("\n2. RM - Análisis de patrones:")
print("Missing RM por AGE (edificios antiguos vs nuevos):")
age_groups = pd.cut(df['AGE'], bins=3, labels=['New', 'Medium', 'Old'])
print(df.groupby(age_groups)['RM'].apply(lambda x: x.isnull().sum()))

# 3. MEDV: ¿MNAR?
print("\n3. MEDV - Análisis de patrones:")
price_missing = df['MEDV'].isnull()
print("Valores de MEDV en registros con missing:")
print(df[price_missing]['MEDV'].describe())  # estadísticas descriptivas

# Análisis de correlación entre missing y otras variables
print("\nCorrelación entre missing de MEDV y variables socioeconómicas:")
missing_corr = df[price_missing][['CRIM', 'INDUS', 'NOX', 'AGE']].mean()
print(missing_corr)


In [ ]:
# === DETECCIÓN DE OUTLIERS CON IQR ===
# "Detectar extremos usando mediana y cuartiles"
# "Cuándo usar: distribuciones asimétricas / colas pesadas / presencia de outliers"

def detect_outliers_iqr(df, column, factor=1.5):
    """Outliers por IQR. Devuelve (df_outliers, lower, upper)."""
    x = pd.to_numeric(df[column], errors="coerce")
    x_no_na = x.dropna().astype(float).values
    if x_no_na.size == 0:
        # sin datos válidos
        return df.iloc[[]], np.nan, np.nan
    q1 = np.percentile(x_no_na, 25)
    q3 = np.percentile(x_no_na, 75)
    iqr = q3 - q1
    lower = q1 - factor * iqr
    upper = q3 + factor * iqr
    mask = (pd.to_numeric(df[column], errors="coerce") < lower) | (pd.to_numeric(df[column], errors="coerce") > upper)
    return df[mask], lower, upper

# Analizar outliers en columnas numéricas principales
numeric_columns = ['MEDV', 'CRIM', 'RM', 'AGE', 'NOX', 'LSTAT', 'PTRATIO']
outlier_analysis = {}

for col in numeric_columns:
    if col in df.columns and not df[col].isnull().all():  # método para verificar si hay missing data
        outliers, lower, upper = detect_outliers_iqr(df, col)
        outlier_analysis[col] = {
            'count': len(outliers),
            'percentage': (len(outliers) / len(df)) * 100,
            'lower_bound': lower,
            'upper_bound': upper
        }

outlier_df = pd.DataFrame(outlier_analysis).T
print("=== ANÁLISIS DE OUTLIERS (IQR) ===")
print("Útil cuando la distribución está chueca o con colas largas")
print(outlier_df)

# Análisis adicional de outliers
print("\n=== RESUMEN DE OUTLIERS ===")
total_outliers = outlier_df['count'].sum()  # método para sumar outliers
print(f"Total de outliers detectados: {total_outliers}")
print(f"Porcentaje promedio de outliers: {outlier_df['percentage'].mean():.2f}%")  # método para calcular media
print(f"Columna con más outliers: {outlier_df['count'].idxmax()}")  # método para encontrar máximo


In [ ]:
# === DETECCIÓN DE OUTLIERS CON Z-SCORE ===
# "Cuándo usar: distribución aprox. campana y sin colas raras"
# "Regla: 3 pasos (desvios) desde el promedio = raro"

def detect_outliers_zscore(df, column, threshold=3):
    """Detectar outliers usando Z-Score - Regla: 3 desvios desde el promedio = raro"""
    from scipy import stats
    z_scores = np.abs(stats.zscore(df[column].dropna()))
    outlier_indices = df[column].dropna().index[z_scores > threshold]
    return df.loc[outlier_indices]

# Comparar métodos de detección
print("\n=== COMPARACIÓN DE MÉTODOS DE DETECCIÓN ===")
for col in ['MEDV', 'CRIM', 'RM', 'AGE']:
    if col in df.columns and not df[col].isnull().all():
        iqr_outliers = detect_outliers_iqr(df, col)
        zscore_outliers = detect_outliers_zscore(df, col)

        print(f"\n{col}:")
        print(f"  IQR outliers: {len(iqr_outliers[0])} ({len(iqr_outliers[0])/len(df)*100:.1f}%)")
        print(f"  Z-Score outliers: {len(zscore_outliers)} ({len(zscore_outliers)/len(df)*100:.1f}%)")


In [ ]:
# === VISUALIZAR OUTLIERS ===

cols = ['MEDV', 'CRIM', 'RM', 'AGE']

fig, axes = plt.subplots(2, 2, figsize=(15, 12))  # función para crear subplots
axes = axes.flatten()  # método para aplanar array

for i, col in enumerate(cols):
    if col not in df.columns:
        axes[i].set_visible(False)
        continue

    # convertir a numérico de forma segura
    y = pd.to_numeric(df[col], errors='coerce').dropna()

    if y.empty:
        axes[i].axis('off')
        axes[i].text(0.5, 0.5, f"{col}: sin datos numéricos", ha='center', va='center', fontsize=11)
        continue

    # Boxplot usando el vector numérico (evita inferencias de dtype de seaborn)
    sns.boxplot(y=y, ax=axes[i])  # función para boxplot
    axes[i].set_title(f'Outliers en {col} - Boston Housing', fontweight='bold')
    axes[i].set_ylabel(col)

    # Outliers por IQR y bandas
    iqr_df, lower, upper = detect_outliers_iqr(df, col)
    out_vals = pd.to_numeric(iqr_df[col], errors='coerce').dropna()

    if np.isfinite(lower):
        axes[i].axhline(lower, linestyle='--', linewidth=1, label='Límite IQR')
    if np.isfinite(upper):
        axes[i].axhline(upper, linestyle='--', linewidth=1)

    # Marcar outliers con un leve jitter en X para que se vean
    if len(out_vals) > 0:
        jitter_x = np.random.normal(loc=0, scale=0.02, size=len(out_vals))
        # Graficar outliers como puntos rojos con jitter en X
        axes[i].scatter(jitter_x + 0.05, out_vals, alpha=0.6, s=50, color='red', label=f'Outliers ({len(out_vals)})')
        axes[i].legend()  # método para mostrar leyenda

    # Opcional: si la variable es muy sesgada, usar escala log
    if col in ['CRIM', 'MEDV'] and y.skew() > 1:
        axes[i].set_yscale('log')
        axes[i].set_title(f'Outliers en {col} (escala log)', fontweight='bold')

plt.tight_layout() # función para ajustar layout
plt.savefig('boston-housing-outliers-analysis.png', dpi=300, bbox_inches='tight') # función para guardar
plt.show() # función para mostrar gráfico


In [ ]:
# === IMPLEMENTAR ESTRATEGIAS DE IMPUTACIÓN ===
# "Rellenar no es gratis; hacelo columna a columna y documentá"
# "Num: mediana (si cola pesada) / media (si ~normal)"
# "Cat: moda o 'Unknown' (+ flag si sospecha MNAR)"

def impute_missing_data(df, strategy='median'):
    """Implementar diferentes estrategias de imputación - Reglas simples de la clase"""
    df_imputed = df.copy()

    for col in df.columns:
        if df[col].isnull().any():
            if df[col].dtype in ['int64', 'float64']:
                if strategy == 'mean':
                    df_imputed[col].fillna(df[col].mean(), inplace=True)  # imputar con media
                elif strategy == 'median':
                    df_imputed[col].fillna(df[col].median(), inplace=True)  # imputar con mediana
                elif strategy == 'mode':
                    df_imputed[col].fillna(df[col].mode()[0], inplace=True)  # imputar con moda
            else:
                # Para variables categóricas
                df_imputed[col].fillna(df[col].mode()[0], inplace=True)  # imputar con moda

    return df_imputed

# Probar diferentes estrategias
strategies = ['mean', 'median', 'mode']
imputed_datasets = {}

for strategy in strategies:
    imputed_datasets[strategy] = impute_missing_data(df, strategy)
    print(f"Estrategia {strategy}: {imputed_datasets[strategy].isnull().sum().sum()} missing values restantes")


In [ ]:
# === ANTI-LEAKAGE BÁSICO ===
# "No espiés el examen: fit en TRAIN, transform en VALID/TEST"
# "Split: X_train / X_valid / X_test"
# "imputer.fit(X_train) → transform al resto"

from sklearn.model_selection import train_test_split

# 1. Split de datos (ANTES de imputar)
X = df.drop('MEDV', axis=1)  # features
y = df['MEDV']  # target

X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.4, random_state=42)
X_valid, X_test, y_valid, y_test = train_test_split(X_temp, y_temp, test_size=0.5, random_state=42)

print("=== SPLIT DE DATOS ===")
print(f"Train: {X_train.shape[0]} registros")
print(f"Valid: {X_valid.shape[0]} registros") 
print(f"Test: {X_test.shape[0]} registros")

# 2. Imputar SOLO en train, luego transformar
from sklearn.impute import SimpleImputer

# Separar columnas numéricas y categóricas
numeric_columns = X_train.select_dtypes(include=[np.number]).columns.tolist()
categorical_columns = X_train.select_dtypes(include=['object']).columns.tolist()

print(f"Columnas numéricas: {len(numeric_columns)}")
print(f"Columnas categóricas: {len(categorical_columns)}")

# Crear imputers para cada tipo de dato
numeric_imputer = SimpleImputer(strategy='median')  # estrategia para numéricas
categorical_imputer = SimpleImputer(strategy='most_frequent')  # estrategia para categóricas

# Ajustar imputers SOLO con train
numeric_imputer.fit(X_train[numeric_columns])  # ajustar numéricas
categorical_imputer.fit(X_train[categorical_columns])  # ajustar categóricas

# Transformar todos los conjuntos
X_train_numeric = numeric_imputer.transform(X_train[numeric_columns])  # transformar numéricas
X_train_categorical = categorical_imputer.transform(X_train[categorical_columns])  # transformar categóricas

X_valid_numeric = numeric_imputer.transform(X_valid[numeric_columns])
X_valid_categorical = categorical_imputer.transform(X_valid[categorical_columns])

X_test_numeric = numeric_imputer.transform(X_test[numeric_columns])
X_test_categorical = categorical_imputer.transform(X_test[categorical_columns])

print("\n✅ Anti-leakage aplicado: fit solo en train, transform en todo")


# 🎯 Parte B: Análisis Crítico

### 1. ¿Qué tipo de *missing data* identificaste en cada columna? Justifica tu clasificación.
- **NOX** → **MCAR**. No depende de ninguna variable observable.  
- **RM** → **MAR**. El missing está asociado a la variable "AGE" (edificios más antiguos tienen más missing de habitaciones).
- **MEDV** → **MNAR**. Los datos faltantes se concentran en propiedades de alto precio (los valores faltan porque dependen del propio valor de la variable).

### 2. ¿Por qué elegiste esas estrategias de imputación específicas? ¿Qué alternativas consideraste?
- Para **numéricas**, usamos mediana, porque es robusta frente a outliers en el mercado inmobiliario.
- Para **categóricas**, usamos moda, porque mantiene consistencia con las categorías más comunes.  
- Algunas alternativas:  
  - Imputación con modelos predictivos como: KNN Imputer y regresiones.
  - Variables "flag" indicando si un valor fue imputado.
  - Eliminación de registros con demasiados missing data. 

### 3. ¿Cómo podrían las decisiones de imputación afectar a diferentes grupos demográficos? (ej: barrios, tipos de vivienda)
- Para "RM", usar la mediana podría sesgar los resultados hacia tipos de vivienda con más habitaciones, afectando la representación de viviendas pequeñas.
- Generaríamos sesgos socioeconómicos, afectando predicciones de modelos que influyan en decisiones como crédito hipotecario e impuestos inmobiliarios. 

### 4. ¿Qué información adicional necesitarías para tomar mejores decisiones sobre los outliers?
- Mayor contexto sobre el mercado inmobiliario de Boston, variables externas como tasas de interés y también un historial de los precios del mercado para años anteriores.

### 5. ¿Cómo garantizas que tu pipeline sea reproducible y transparente?
- Uso de scripts/notebooks versionados en GitHub con fecha y autores de los mismos. 
- Documentación de cada paso, justificando cada decisión.  
- Guardado de outputs intermedios (tablas limpias, gráficos) en carpetas organizadas.  
- Flags de imputación para diferenciar valores originales de los imputados.  
- Usar pipelines de sklearn para que el proceso sea automatizado y pueda aplicarse en nuevos datasets sin pasos manuales.

---
